First, check we are in the main project directory:

In [1]:
from os import getcwd
print(getcwd())

/Users/u1874623/Documents/GitHub/covid-19-in-households-public/tutorials


If we are instead in the `tutorials` subdirectory, move up to it by uncommenting this line:

In [2]:
cd ..

/Users/u1874623/Documents/GitHub/covid-19-in-households-public


Import functions etc:

In [3]:
from argparse import ArgumentParser
from os import mkdir
from os.path import isdir, isfile
from pickle import load, dump
from copy import deepcopy
from multiprocessing import Pool
from numpy import append, arange, array, exp, log, ones, sum, vstack, where
from numpy.linalg import eig
from numpy.random import rand
from pandas import read_csv
from time import time as get_time
from scipy.integrate import solve_ivp, trapezoid
from matplotlib.pyplot import subplots
from matplotlib.cm import get_cmap
from model.preprocessing import (add_vuln_class, add_vulnerable_hh_members,
estimate_beta_ext, HouseholdPopulation, make_initial_condition_by_eigenvector,
map_SEPIR_to_SEPIRQ,SEPIRInput, SEPIRQInput)
from model.common import SEPIRRateEquations, SEPIRQRateEquations
from model.imports import NoImportModel
from model.specs import (TWO_AGE_UK_SPEC, TWO_AGE_EXT_SEPIRQ_SPEC,
TWO_AGE_SEPIR_SPEC_FOR_FITTING)

Constants and functions we need to run the analysis:

In [4]:
if isdir('outputs/oohi') is False:
    mkdir('outputs/oohi')

DOUBLING_TIME = 10
growth_rate = log(2) / DOUBLING_TIME

SEPIR_SPEC = {**TWO_AGE_SEPIR_SPEC_FOR_FITTING, **TWO_AGE_UK_SPEC}
OOHI_SPEC = {**TWO_AGE_UK_SPEC, **TWO_AGE_EXT_SEPIRQ_SPEC}

relative_iso_rates = [1.0, 1.0, 0.5]

vuln_ext_scale = 0


# List of observed household compositions
composition_list = read_csv(
    'inputs/eng_and_wales_adult_child_vuln_composition_list.csv',
    header=0).to_numpy()
# Proportion of households which are in each composition
comp_dist = read_csv(
    'inputs/eng_and_wales_adult_child_vuln_composition_dist.csv',
    header=0).to_numpy().squeeze()

if isfile('outputs/oohi/beta_ext.pkl') is True:
    with open('outputs/oohi/beta_ext.pkl', 'rb') as f:
        beta_ext = load(f)
else:
    # List of observed household compositions
    fitting_comp_list = read_csv(
        'inputs/eng_and_wales_adult_child_composition_list.csv',
        header=0).to_numpy()
    # Proportion of households which are in each composition
    fitting_comp_dist = read_csv(
        'inputs/eng_and_wales_adult_child_composition_dist.csv',
        header=0).to_numpy().squeeze()
    model_input_to_fit = SEPIRInput(SEPIR_SPEC,
                                    fitting_comp_list,
                                    fitting_comp_dist)
    household_population_to_fit = HouseholdPopulation(
        fitting_comp_list, fitting_comp_dist, model_input_to_fit)
    print('number of states for 2-class pop is',
            household_population_to_fit.Q_int.shape)
    rhs_to_fit = SEPIRRateEquations(model_input_to_fit,
                                    household_population_to_fit,
                                    NoImportModel(5,2))
    beta_ext = estimate_beta_ext(household_population_to_fit,
                                 rhs_to_fit,
                                 growth_rate)
    with open('outputs/oohi/beta_ext.pkl', 'wb') as f:
        dump(beta_ext, f)

vuln_prop = 2.2/56
adult_class = 1

import_model = NoImportModel(6,3)

prev=1.0e-3 # Starting prevalence
starting_immunity=1e-2 # Starting antibody prev/immunity

Set up the analysis:

In [5]:
pre_npi_input =  SEPIRInput(SEPIR_SPEC,
                                 composition_list,
                                 comp_dist)
pre_npi_input.k_ext *= beta_ext
pre_npi_input = add_vuln_class(pre_npi_input,
                    vuln_prop,
                    adult_class,
                    vuln_ext_scale)
pre_npi_household_population = HouseholdPopulation(
    composition_list, comp_dist, pre_npi_input)
pre_npi_rhs = SEPIRRateEquations(
    pre_npi_input,
    pre_npi_household_population,
    import_model)
H0_pre_npi = make_initial_condition_by_eigenvector(
                                    growth_rate,
                                    pre_npi_input,
                                    pre_npi_household_population,
                                    pre_npi_rhs,
                                    prev,
                                    starting_immunity)


if isfile('outputs/oohi/map_matrix.pkl') is True:
    with open('outputs/oohi/map_matrix.pkl', 'rb') as f:
        map_matrix = load(f)
else:
    print('calculating map matrix...')
    basic_npi_spec = deepcopy(OOHI_SPEC)
    basic_npi_input = SEPIRQInput(basic_npi_spec,
                                composition_list,
                                comp_dist)
    basic_npi_input.k_ext = beta_ext * basic_npi_input.k_ext
    basic_npi_input = add_vuln_class(basic_npi_input,
                        vuln_prop,
                        adult_class,
                        vuln_ext_scale)
    basic_npi_population = HouseholdPopulation(
        composition_list, comp_dist, basic_npi_input)
    map_mat_start = get_time()
    map_matrix = map_SEPIR_to_SEPIRQ(
                                pre_npi_household_population,
                                basic_npi_population)
    print('map matrix calculation took',
            (get_time()-map_mat_start),
            'seconds')
    map_matrix = map_matrix
    with open('outputs/oohi/map_matrix.pkl', 'wb') as f:
                dump(map_matrix, f)

/Users/u1874623/opt/anaconda3/lib/python3.8/site-packages/scipy/sparse/linalg/dsolve/linsolve.py:407: SparseEfficiencyWarning: splu requires CSC matrix format
  warn('splu requires CSC matrix format', SparseEfficiencyWarning)


Precondtioner computed in 0.12577199935913086s
multiplier calculation took 1.7292578220367432 seconds.


Do the analysis:

In [6]:
iso_rate = 1/5 # Cases identified on average within 5 days of infection
iso_prob = 0 # Turn off isolation by setting adherence probability to zero

p = [iso_rate, iso_prob]

In [7]:
start_time = get_time()

this_spec = deepcopy(OOHI_SPEC)
this_spec['exp_iso_rate'] = p[0] * relative_iso_rates[0] * ones(2,)
this_spec['pro_iso_rate'] = p[0] * relative_iso_rates[1] * ones(2,)
this_spec['inf_iso_rate'] = p[0] * relative_iso_rates[2] * ones(2,)
this_spec['ad_prob'] = p[1]
model_input = SEPIRQInput(this_spec, composition_list, comp_dist)
model_input.k_ext = beta_ext * model_input.k_ext
model_input = add_vuln_class(model_input,
                    vuln_prop,
                    adult_class,
                    vuln_ext_scale)

household_population = HouseholdPopulation(
    composition_list, comp_dist, model_input)
rhs = SEPIRQRateEquations(
    model_input,
    household_population,
    import_model)

H0_iso = H0_pre_npi * map_matrix

'''Record the starting state for future reference:'''

S0 = H0_iso.T.dot(household_population.states[:, ::6]) / \
                model_input.ave_hh_by_class
E0 = H0_iso.T.dot(household_population.states[:, 1::6]) / \
                model_input.ave_hh_by_class
P0 = H0_iso.T.dot(household_population.states[:, 2::6]) / \
                model_input.ave_hh_by_class
I0 = H0_iso.T.dot(household_population.states[:, 3::6]) / \
                model_input.ave_hh_by_class
R0 = H0_iso.T.dot(household_population.states[:, 4::6]) / \
                model_input.ave_hh_by_class
Q0 = H0_iso.T.dot(household_population.states[:, 5::6]) / \
                model_input.ave_hh_by_class


no_days = 100
tspan = (0.0, no_days)
solution = solve_ivp(rhs,
                     tspan,
                     H0_iso,
                     first_step=0.001,
                     atol=1e-16)

t = solution.t
H = solution.y

print('Calculations took', (get_time()-start_time), 'seconds.')

infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 0 0]
new_state= [0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 0 0 0 0 1]
new_state= [0 1 0 0 0 0 0 0 0 0 0 1]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 0 0 0 1 0]
new_state= [0 1 0 0 0 0 0 0 0 0 1 0]
infection in vuln class, rate 0.09110216248599852
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 0 0 1 0 0]
new_state= [0 1 0 0 0 0 0 0 0 1 0 0]
infection in vuln class, rate 0.04555108124299926
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 0 1 0 0 0]
new_state= [0 1 0 0 0 0 0 0 1 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 1 0 0 0 0]
new_state= [0 1 0 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 1 0 0 0 0 0]
new_state= [0 1 0 0 0 0 1 0 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 1 0 0 0 0 0 1]
new_state= [0 1 0 0 0 1 0 0 0 0

infection in vuln class, rate 0.05362019071747984
class_idx= [0 2]
old_state= [1 0 2 0 1 0 0 0 0 0 1 0]
new_state= [0 1 2 0 1 0 0 0 0 0 1 0]
infection in vuln class, rate 0.15166080185938383
class_idx= [0 2]
old_state= [1 0 2 1 0 0 0 0 0 0 1 0]
new_state= [0 1 2 1 0 0 0 0 0 0 1 0]
infection in vuln class, rate 0.09287289463420818
class_idx= [0 2]
old_state= [1 0 3 0 0 0 0 0 0 0 1 0]
new_state= [0 1 3 0 0 0 0 0 0 0 1 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 1 0 0 0 2 0 0 0 0 1 0]
new_state= [0 2 0 0 0 2 0 0 0 0 1 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 1 0 0 1 1 0 0 0 0 1 0]
new_state= [0 2 0 0 1 1 0 0 0 0 1 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 1 0 0 2 0 0 0 0 0 1 0]
new_state= [0 2 0 0 2 0 0 0 0 0 1 0]
infection in vuln class, rate 0.05362019071747984
class_idx= [0 2]
old_state= [1 1 0 1 0 1 0 0 0 0 1 0]
new_state= [0 2 0 1 0 1 0 0 0 0 1 0]
infection in vuln class, rate 0.07583040092969191
class_idx= 

infection in vuln class, rate 0.22749120278907575
class_idx= [0 2]
old_state= [2 0 1 1 0 0 1 0 0 0 0 0]
new_state= [1 1 1 1 0 0 1 0 0 0 0 0]
infection in vuln class, rate 0.12383052617894424
class_idx= [0 2]
old_state= [2 0 2 0 0 0 1 0 0 0 0 0]
new_state= [1 1 2 0 0 0 1 0 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [2 1 0 0 0 1 1 0 0 0 0 0]
new_state= [1 2 0 0 0 1 1 0 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [2 1 0 0 1 0 1 0 0 0 0 0]
new_state= [1 2 0 0 1 0 1 0 0 0 0 0]
infection in vuln class, rate 0.12383052617894424
class_idx= [0 2]
old_state= [2 1 0 1 0 0 1 0 0 0 0 0]
new_state= [1 2 0 1 0 0 1 0 0 0 0 0]
infection in vuln class, rate 0.05362019071747984
class_idx= [0 2]
old_state= [2 1 1 0 0 0 1 0 0 0 0 0]
new_state= [1 2 1 0 0 0 1 0 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [2 2 0 0 0 0 1 0 0 0 0 0]
new_state= [1 3 0 0 0 0 1 0 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state=

old_state= [1 1 1 1 0 1 0 0 0 0 1 0]
new_state= [0 2 1 1 0 1 0 0 0 0 1 0]
infection in vuln class, rate 0.07193903484647288
class_idx= [0 2]
old_state= [1 1 1 1 1 0 0 0 0 0 1 0]
new_state= [0 2 1 1 1 0 0 0 0 0 1 0]
infection in vuln class, rate 0.11989839141078815
class_idx= [0 2]
old_state= [1 1 1 2 0 0 0 0 0 0 1 0]
new_state= [0 2 1 2 0 0 0 0 0 0 1 0]
infection in vuln class, rate 0.05362019071747984
class_idx= [0 2]
old_state= [1 1 2 0 0 1 0 0 0 0 1 0]
new_state= [0 2 2 0 0 1 0 0 0 0 1 0]
infection in vuln class, rate 0.047959356564315256
class_idx= [0 2]
old_state= [1 1 2 0 1 0 0 0 0 0 1 0]
new_state= [0 2 2 0 1 0 0 0 0 0 1 0]
infection in vuln class, rate 0.09591871312863051
class_idx= [0 2]
old_state= [1 1 2 1 0 0 0 0 0 0 1 0]
new_state= [0 2 2 1 0 0 0 0 0 0 1 0]
infection in vuln class, rate 0.07193903484647288
class_idx= [0 2]
old_state= [1 1 3 0 0 0 0 0 0 0 1 0]
new_state= [0 2 3 0 0 0 0 0 0 0 1 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 2 0 0 0 2 0 0 

old_state= [1 1 1 0 1 1 0 0 1 0 0 0]
new_state= [0 2 1 0 1 1 0 0 1 0 0 0]
infection in vuln class, rate 0.06953075952515689
class_idx= [0 2]
old_state= [1 1 1 0 2 0 0 0 1 0 0 0]
new_state= [0 2 1 0 2 0 0 0 1 0 0 0]
infection in vuln class, rate 0.12598136731921902
class_idx= [0 2]
old_state= [1 1 1 1 0 1 0 0 1 0 0 0]
new_state= [0 2 1 1 0 1 0 0 1 0 0 0]
infection in vuln class, rate 0.11749011608947213
class_idx= [0 2]
old_state= [1 1 1 1 1 0 0 0 1 0 0 0]
new_state= [0 2 1 1 1 0 0 0 1 0 0 0]
infection in vuln class, rate 0.1654494726537874
class_idx= [0 2]
old_state= [1 1 1 2 0 0 0 0 1 0 0 0]
new_state= [0 2 1 2 0 0 0 0 1 0 0 0]
infection in vuln class, rate 0.09917127196047909
class_idx= [0 2]
old_state= [1 1 2 0 0 1 0 0 1 0 0 0]
new_state= [0 2 2 0 0 1 0 0 1 0 0 0]
infection in vuln class, rate 0.09351043780731452
class_idx= [0 2]
old_state= [1 1 2 0 1 0 0 0 1 0 0 0]
new_state= [0 2 2 0 1 0 0 0 1 0 0 0]
infection in vuln class, rate 0.14146979437162976
class_idx= [0 2]
old_state= [1 

...

infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 0 4]
new_state= [0 1 0 0 0 4]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 1 3]
new_state= [0 1 0 0 1 3]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 2 2]
new_state= [0 1 0 0 2 2]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 3 1]
new_state= [0 1 0 0 3 1]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 4 0]
new_state= [0 1 0 0 4 0]
infection in vuln class, rate 0.030742072369851287
class_idx= [2]
old_state= [1 0 0 1 0 3]
new_state= [0 1 0 1 0 3]
infection in vuln class, rate 0.06874136358820554
class_idx= [2]
old_state= [1 0 0 1 1 2]
new_state= [0 1 0 1 1 2]
infection in vuln class, rate 0.048607484341230155
class_idx= [2]
old_state= [1 0 0 1 2 1]
new_state= [0 1 0 1 2 1]
infection in vuln class, rate 0.039687844772112416
class_idx= [2]
old_state= [1 0 0 1 3 0]
new_state= [0 1 0 1 3 0]
infection in vuln class, rate 0.0687413635

new_state= [0 1 0 0 0 0 0 3 2 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 4 0 0 0 1]
new_state= [0 1 0 0 0 0 0 4 0 0 0 1]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 4 0 0 1 0]
new_state= [0 1 0 0 0 0 0 4 0 0 1 0]
infection in vuln class, rate 0.04074212564318478
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 4 0 1 0 0]
new_state= [0 1 0 0 0 0 0 4 0 1 0 0]
infection in vuln class, rate 0.02037106282159239
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 4 1 0 0 0]
new_state= [0 1 0 0 0 0 0 4 1 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 0 5 0 0 0 0]
new_state= [0 1 0 0 0 0 0 5 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 1 0 0 0 0 4]
new_state= [0 1 0 0 0 0 1 0 0 0 0 4]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 0 1 0 0 0 1 3]
new_state= [0 1 0 0 0 0 1 0 0 0 1 3]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_s

infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 0 0 5]
new_state= [0 1 0 0 0 0 0 0 0 0 0 5]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 0 1 4]
new_state= [0 1 0 0 0 0 0 0 0 0 1 4]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 0 2 3]
new_state= [0 1 0 0 0 0 0 0 0 0 2 3]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 0 3 2]
new_state= [0 1 0 0 0 0 0 0 0 0 3 2]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 0 4 1]
new_state= [0 1 0 0 0 0 0 0 0 0 4 1]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 0 5 0]
new_state= [0 1 0 0 0 0 0 0 0 0 5 0]
infection in vuln class, rate 0.06874136358820554
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 1 0 4]
new_state= [0 1 0 0 0 0 0 0 0 1 0 4]
infection in vuln class, rate 0.06874136358820554
class_idx= [1 2]
old_state= [1 0 0 0 0 0 0 0 0 1 1 3]
new_s

infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 0 5]
new_state= [0 1 0 0 0 5]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 1 4]
new_state= [0 1 0 0 1 4]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 2 3]
new_state= [0 1 0 0 2 3]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 3 2]
new_state= [0 1 0 0 3 2]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 4 1]
new_state= [0 1 0 0 4 1]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 5 0]
new_state= [0 1 0 0 5 0]
infection in vuln class, rate 0.028063544169039757
class_idx= [2]
old_state= [1 0 0 1 0 4]
new_state= [0 1 0 1 0 4]
infection in vuln class, rate 0.06874136358820554
class_idx= [2]
old_state= [1 0 0 1 1 3]
new_state= [0 1 0 1 1 3]
infection in vuln class, rate 0.048607484341230155
class_idx= [2]
old_state= [1 0 0 1 2 2]
new_state= [0 1 0 1 2 2]
infection in vuln class, rate 0.039687844772112416
class_id

Calculations took 51.5035080909729 seconds.


Calculate outputs:

In [8]:
S = H.T.dot(household_population.states[:, ::6])
E = H.T.dot(household_population.states[:, 1::6])
P = H.T.dot(household_population.states[:, 2::6])
I = H.T.dot(household_population.states[:, 3::6])
R = H.T.dot(household_population.states[:, 4::6])
Q = H.T.dot(household_population.states[:, 5::6])

E_vuln_present = \
    H[
        where(household_population.composition_by_state[:,2]>0)[0],
        :].T.dot(
        household_population.states[
            where(household_population.composition_by_state[:,2]>0)[0],
            1::6]
        )
I_vuln_present = \
    H[
        where(household_population.composition_by_state[:,2]>0)[0],
        :].T.dot(
        household_population.states[
            where(household_population.composition_by_state[:,2]>0)[0],
            3::6]
        )

vuln_peak = 100 * max(I[:, 2]) / \
                model_input.ave_hh_by_class[2]
vuln_end = 100 * R[-1, 2] / \
                model_input.ave_hh_by_class[2]
iso_peak = 100 * max(Q.sum(axis=1)) / model_input.ave_hh_size
Q_all = Q.sum(axis=1) / model_input.ave_hh_size
cum_iso = 100 * trapezoid(Q_all, t)

Time series of E's and I's restricted to households with at least one vulnerable member:

In [9]:
print('E(at least one vuln present)=',E_vuln_present/model_input.ave_hh_by_class)
print('I(at least one vuln present)=',I_vuln_present/model_input.ave_hh_by_class)

E(at least one vuln present)= [[9.69758130e-05 2.92503230e-05 5.63883779e-29]
 [9.69564212e-05 2.92444739e-05 5.63771014e-29]
 [9.67628741e-05 2.91860893e-05 5.62644599e-29]
 [9.50635151e-05 2.86730263e-05 5.52680759e-29]
 [9.26512583e-05 2.79432980e-05 5.38292267e-29]
 [8.92732974e-05 2.69183448e-05 5.17594095e-29]
 [8.45096345e-05 2.54658904e-05 4.87080315e-29]
 [7.85851713e-05 2.36453091e-05 4.46237114e-29]
 [7.20387187e-05 2.16085243e-05 3.95380081e-29]
 [6.57675439e-05 1.96178314e-05 3.36090540e-29]
 [6.08844418e-05 1.80109551e-05 2.71082203e-29]
 [5.84693790e-05 1.71387716e-05 2.04725945e-29]
 [5.91034655e-05 1.72305620e-05 1.42139330e-29]
 [6.20653414e-05 1.81307101e-05 9.46612254e-30]
 [6.43279011e-05 1.88663201e-05 7.39515078e-30]
 [6.66856077e-05 1.96566606e-05 5.80479304e-30]
 [6.92691648e-05 2.05425025e-05 4.48678234e-30]
 [7.22855956e-05 2.15951808e-05 3.34118855e-30]
 [7.54251126e-05 2.27047551e-05 2.47262060e-30]
 [7.86727576e-05 2.38617241e-05 1.82342793e-30]
 [8.207488

Calculation above suggests infections are present and evolve in households with vulnerable members, but no spread into this class happens.

In the boxes below, we explicitly calculate what our internal transmission matrix thinks the infections into the vulnerable class should look like:

In [10]:
states = household_population.states
Q_int = household_population.Q_int

In [11]:
inf_possible = where(((states[:,1::6]+states[:,2::6]+states[:,3::6]).sum(1)>0)&(states[:,12]>0))[0]

In [12]:
from numpy import zeros
from copy import copy
inf_to = zeros(len(inf_possible),dtype=int)
for k in range(len(inf_possible)):
    old_state = copy(states[inf_possible[k], :])
    new_state = old_state.copy()
    new_state[12] -= 1
    new_state[13] += 1
    inf_to[k] = where(abs(states-new_state).sum(1)==0)[0]

In [13]:
inf_rates = Q_int[inf_possible,inf_to]

In [15]:
print(inf_rates)

[[0.         0.         0.         ... 0.15371036 0.07015886 0.        ]]
